# This is a test notebook to check if spherical model is correct

Let's import libraries first and print versions used

In [1]:
import numpy as np
from math import cos, sin, pi, exp, atan
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import matplotlib.pyplot as plt
import matplotlib as mpl

print('\n'.join(f'{m.__name__}=={m.__version__}' for m in globals().values() if getattr(m, '__version__', None)))

numpy==1.20.1
matplotlib==3.3.4


## Functions

Now we can create recently derived spherical geometry case

In [2]:
"""
    d_sphere_P(r:np.array,θ:np.array,φ:np.array,x0:float,y0:float,z0:float,μ0:float)
    In the spherical geometry, e.g. droplet, this function computes the distance from any
    point M:(r,θ,φ) in the sample to the surface in direction to some point P:(x0,y0,z0).
    Note: M is given in spherical coordinates and P in Cartesian coordinates.
    Oz is along the photon beam. Center of the droplet is in the center of coordinates.
    θ is taken between Oz and the project of M onto the plane xOz, φ between M and Oy, and r = √(x^2+y^2+z^2)
    μ0 is the radius of the sphere
"""
def d_sphere_P(r, θ, φ, x0, y0, z0, μ0):
    dp = np.zeros((len(r), len(θ), len(φ)))
    for i, R in enumerate(r):
        for j, Ө in enumerate(θ):
            for k, Φ in enumerate(φ):
                ## M coordinates from spherical to cartesian system
                xm = R*cos(Ө)*sin(Φ)
                ym = R*sin(Ө)*sin(Φ)
                zm = R*cos(Φ)

                ## compute all cos/sin
                cosω = (x0-xm) / ((x0-xm)**2 + (y0-ym)**2)**.5
                sinω = (y0-ym) / ((x0-xm)**2 + (y0-ym)**2)**.5
                    
                cosβ = ((x0-xm)**2 + (y0-ym)**2)**.5 / ((x0-xm)**2 + (y0-ym)**2 + (z0-zm)**2)**.5
                sinβ = (z0-zm) / ((x0-xm)**2 + (y0-ym)**2 + (z0-zm)**2)**.5
                    
                cosα = sin(Φ) * cosβ * (
                    cos(Ө) * cosω + sin(Ө) * sinω) + cos(Φ) * sinβ

                dp[i,j,k] =  (μ0**2 - R**2 * (1-cosα**2))**.5 - R * cosα
    return dp


"""
    sphere_gain_H(r:np.array,θ:np.array,φ:np.array,x0:float,y0:float,z0:float,μ0:float,λe:float)
    Compute the volume integrales (exact for piecewise linear gain)
    H_{n,j,k} = ∭ e_i(r)e_j(θ)e_k(φ) e^{-d_P(M)/λe} r^2drdθdφ
    The arrays r, θ and φ are the discretization subdivisions
    P:(x0,y0,z0) is the point in Cartesian coordinates used for the computation of the distance d_P
    μ0 is the radius of the sphere
    λe is the attenuation length in the Beer-Lambert model
    Note: does not include the profile of the beam light, but it can be add easily if known
"""
def sphere_gain_H(r, θ, φ, x0, y0, z0, μ0, λe):
    Ari = 0.5 * r**2 * np.diff(r, append=(2*r[-1] - r[-2]))
    Aθj = 0.5 * np.diff(θ, append=(2*θ[-1] - θ[-2]))
    Aφk = 0.5 * np.diff(φ, append=(2*φ[-1] - φ[-2]))
    
    dp = d_sphere_P(r, θ , φ, x0, y0, z0, μ0)
    H_rθφ = np.zeros((len(Ari), len(Aθj), len(Aφk)))
    H_r = np.zeros((len(Ari), len(Aθj), len(Aφk)))
    for i in range(len(Ari)):
        for j in range(len(Aθj)):
            for k in range(len(Aφk)):
                H_rθφ[i,j,k] = exp(-1*dp[i,j,k]/λe)
                H_r[i,j,k] = Ari[i] * Aθj[j] * Aφk[k] * H_rθφ[i,j,k]
    
    return H_r, H_rθφ, Ari, Aθj, Aφk

## 3D plots

In [3]:
μ0 = 20.0   # radius
λe = 2.0e-3 # μ0; # EAL
L = 3 * μ0  #

J = 64 # discretisation

r = np.linspace(μ0-10*λe, μ0, 2) 
θ = np.linspace(0, 2*pi, J)
φ = np.linspace(0, pi, J)

x = np.zeros((len(r), len(θ), len(φ)))
y = np.zeros((len(r), len(θ), len(φ)))
z = np.zeros((len(r), len(θ), len(φ)))

for i, R in enumerate(r):
    for j, Ө in enumerate(θ):
        for k, Φ in enumerate(φ):
            x[i,j,k] = R*cos(Ө)*sin(Φ)
            y[i,j,k] = R*sin(Ө)*sin(Φ)
            z[i,j,k] = R*cos(Φ)

# magic angle: atan(sqrt(2.0),1.0)
# near the analyzer
x0_near = 21;
y0_near = 0.0;
z0_near = 21;

## compute distances
DD = d_sphere_P(r, θ , φ, x0_near, y0_near, z0_near, μ0)
Hr = sphere_gain_H(r, θ, φ, x0_near, y0_near, z0_near, μ0, λe)[0];

In [4]:
fig = make_subplots(rows=1, cols=1,
                    specs=[[{'type': 'scatter3d'}]],
                    horizontal_spacing = 0.01,
                    vertical_spacing = 0.1)

for i in range(len(x)):
    for j in range(len(x[i])):
        if i == 0 and j == 0:
            colorbar = dict(title='Dp', orientation='v')
            legend = True
        else:
            colorbar = None
            legend = False
            
        # plot sphere
        fig.add_trace(
            go.Scatter3d(x=x[i,j], y=y[i,j], z=z[i,j],
                         mode='markers',
                         name='Sphere',
                         showlegend = legend,
                         marker=dict(
                                     size=5,
                                     color=DD[i,j],
                                     colorscale='Viridis',
                                     colorbar=colorbar,
                                     opacity=1
            )),
            row=1, col=1)


## plot dot
fig.add_trace(
    go.Scatter3d(x=[x0_near], y=[y0_near], z=[z0_near],
                name='Detector',
                mode='markers',
                marker=dict(size=12, color='red')),
    row=1, col=1)


fig.update_layout(legend=dict(yanchor="top", y=1.01, xanchor="left", x=0)) # add legend and show plot

In [5]:
fig = plt.figure(figsize=(7,7))
ax = plt.axes(projection='3d')

ax.scatter(x0_near, y0_near, z0_near, c='red', s=20)
ax.scatter(x, y, z, c=DD)
ax.set_xlim(-30,30)
ax.set_ylim(-30,30)
ax.set_zlim(-30,30);

#ax.view_init(90, 180);

## 2D plots

Let's plot distances and gain

In [6]:
μ0 = 20.0   # radius
λe = 2.0e-3 # μ0; # EAL
L = 3 * μ0  #

# magic angle: atan(sqrt(2.0)/1.0)
# far from the analyzer
x0_far = 200.0*np.sqrt(2.0);
y0_far = 0.0;
z0_far = 200.0;

φ0_far  = atan(x0_far/z0_far)
θ0_far  = atan(y0_far/x0_far)

J = 65 # discretisation

## general discretisation
r = np.linspace(0, μ0, J) 
θ = np.linspace(θ0_far-pi, θ0_far+pi, J)
φ = np.linspace(φ0_far - pi/2, φ0_far + 3*pi/2, J)

## model specific discretization
r_surf = np.linspace(μ0-3*λe, μ0, J)
θ_far   = np.linspace(θ0_far-pi, θ0_far+pi, J)
φ_far = np.linspace(φ0_far - pi/2, φ0_far + pi/2, J)

## calculate dp and Hr
DD = d_sphere_P(r, θ, φ, x0_far, y0_far, z0_far, μ0)
Hr = sphere_gain_H(r_surf, θ_far, φ_far, x0_far, y0_far, z0_far, μ0, λe)[0];

In [7]:
fig = plt.figure(figsize=[9,5], dpi=120)

## create axes for distance
ax1 = plt.subplot(121,polar=True)
ax1.set_rlabel_position(-120)
ax1.set_rticks(np.arange(0, μ0 + 1, 5))

## create legend
ax1.plot(atan(x0_far/z0_far)*np.ones(2),[0, μ0], color="red",label=r"$\theta\simeq54.7$")
ax1.legend(loc="lower left", bbox_to_anchor=(.55 + cos(atan(x0_far/z0_far))/2, .55 + sin(atan(x0_far/z0_far))/2))

pcm1 = ax1.pcolormesh(φ, r, DD[:,J//2,:], edgecolors="face", shading='gouraud')

## create colorbar
cax1 = ax1.inset_axes([0.1, .3, 0.05, 0.37], transform=ax1.transAxes)  # change position
cb1 = fig.colorbar(pcm1, orientation="vertical",
                   cax=cax1, shrink=0.6)                               # create bar
cb1.set_label("distance [μm]", fontsize=10)                              # set label

## create axes for gain
ax2 = plt.subplot(122,polar=True)
ax2.set_rlabel_position(-120)
ax2.set_rticks([μ0-0.03, μ0-0.02, μ0-0.01, μ0])

## create legend
ax2.plot(atan(x0_far/z0_far)*np.ones(2),[μ0-0.03, μ0], color="red",label=r"$\theta\simeq54.7$")
ax2.legend(loc="lower left", bbox_to_anchor=(.55 + cos(atan(x0_far/z0_far))/2, .55 + sin(atan(x0_far/z0_far))/2))

pcm2 = ax2.pcolormesh(φ_far, r_surf, Hr[:,J//2,:]/Hr[:,J//2,:].max(), edgecolors="face", shading='gouraud')

## create colorbar
cax2 = ax2.inset_axes([0.1, .3, 0.05, 0.37], transform=ax2.transAxes)  # change position
cb2 = fig.colorbar(pcm2, orientation="vertical",
                   cax=cax2, shrink=0.6)                               # create bar
cb2.set_label("gain [a.u.]", fontsize=10)                              # set label

# annotation and squeezing
plt.tight_layout(pad=1.0, w_pad=2.0, h_pad=0.2)
ax1.annotate('a)', xy=(3, 1),  xycoords="data", xytext=(0.0, 1.0), textcoords="axes fraction", color="black",fontsize=14)
ax1.annotate('b)', xy=(3, 1),  xycoords="data", xytext=(1.39, 1.0), textcoords="axes fraction", color="black",fontsize=14)

# plt.savefig('sphere_distance_gain.pdf')
plt.ylim(μ0-0.03,μ0); # limit y-axes